## Принцип частотно-временной неопределённости сигналов
В этом ноутбуке на примере bandpass-фильтра проиллюстрируем один из фундаментальных принципов обработки сигналов. Он заключается в следующем компромиссе: чем резче мы режем частоты, тем дольше "звенит" сигнал во времени, и наоборот. Либо, по другому: чем точнее локализация во времени, тем она хуже в частотах, и наоборот.

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.fft import fft, fftfreq, ifft
from scipy.signal import convolve
from scipy.ndimage import gaussian_filter1d
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

### 1. Создадим синтетическую трассу с тремя импульсами Рикера разной доминантной частоты и небольшим количеством шума

In [2]:
def ricker_wavelet(f, dt=0.002, n_cycles=6):
    """
    f        : частота (Hz)
    dt       : шаг по времени
    n_cycles : количество периодов волны в окне
    """
    n_points_per_cycle = int(1 / (f * dt))  # сколько отсчетов на период
    length_pts = n_cycles * n_points_per_cycle
    # создаём симметричное окно
    t = np.linspace(-n_cycles/(2*f), n_cycles/(2*f), length_pts)
    y = (1 - 2*(np.pi**2)*(f**2)*(t**2)) * np.exp(-(np.pi**2)*(f**2)*(t**2))
    return t, y


dt = 0.002 # 2 милисекунды на отсчет
nt = 512 # 512 отсчетов
synthetic_trace = np.zeros(nt)

reflection_frequencies = [25, 35, 50]               # Низкая, средняя, высокая частота
reflection_times = [100, 250, 400]                  # Индексы отражений
reflection_amplitudes = [1.0, -1.2, 1.3]            # Амплитуды отражений


# --- Формирование трассы ---
for time_idx, amplitude, freq in zip(reflection_times, reflection_amplitudes, reflection_frequencies):
    _, wavelet = ricker_wavelet(f=freq, dt=dt)
    impulse = np.zeros(nt)
    impulse[time_idx] = amplitude
    trace_component = convolve(impulse, wavelet, mode='same')
    synthetic_trace += trace_component

# --- Добавляем чуточку шума для реалистичности ---
synthetic_trace += np.random.normal(0, 0.01, synthetic_trace.shape)


### 2. Создадим функции для генерации и сглаживания фильтра

In [3]:
def trapezoidal_filter(freqs, f1, f2, f3, f4):
    amp = np.zeros_like(freqs)
    idx1 = np.where((freqs >= f1) & (freqs < f2))
    amp[idx1] = (freqs[idx1] - f1) / (f2 - f1)
    idx2 = np.where((freqs >= f2) & (freqs < f3))
    amp[idx2] = 1.0
    idx3 = np.where((freqs >= f3) & (freqs < f4))
    amp[idx3] = 1.0 - (freqs[idx3] - f3) / (f4 - f3)
    return amp

def smooth_filter(filter_spectrum, N_smooth):
    if N_smooth == 0:
        return filter_spectrum
    sigma = N_smooth / 3.0  # Преобразуем N_smooth в sigma для гауссова фильтра
    y_smooth = gaussian_filter1d(filter_spectrum, sigma=sigma)
    return y_smooth

### 3. Настройка фильтрации и анимации
Зададим 4 частоты для трапециедального фильтра так, чтобы доминантные частоты наших сигналов туда попадали, для чистоты эксперимента. И будем плавно, за 30 итераций, сглаживать нашу трапецию, наблюдая за импульсным откликом фильтра и за фильтрованной трассой

In [4]:
# Параметры
fs = 1.0 / dt # Частота дискретизации
nyquist = 0.5 * fs # Частота Найквиста
n_frames = 30 # Количество кадров анимации
f_corners = [15, 20, 60, 65] # Границы частот для трапециевидного фильтра
max_freq = 125  

# Вычисление статических данных (спектр исходной трассы)
trace_spectrum_abs = np.abs(fft(synthetic_trace))
freqs = fftfreq(nt, dt)
positive_freq_mask = freqs >= 0
freq_mask_125 = (freqs >= 0) & (freqs <= max_freq)  # Маска для частот до 125 Гц

# Вычисление статических данных (спектр исходной трассы)
trace_spectrum_abs = np.abs(fft(synthetic_trace))
freqs = fftfreq(nt, dt)
positive_freq_mask = freqs >= 0

# время для графиков
t = np.arange(nt) * dt

### 4. Создание анимации
На анимации легко увидеть видеть, как за точную локализацию фильтра в частотной области, мы расплачиваемся "звоном" - длинным и осциллирующим импульсным откликом, "размазанным" во времени. И наоборот, при "размазывании" фильтра в частотной области, сигнал фокусируется во временной области, звон исчезает. Это всегда компромисс.

In [5]:
# Создание фигуры и осей для анимации
fig, axs = plt.subplots(2, 2, figsize=(14, 12))
plt.style.use('seaborn-v0_8-whitegrid')

# Добавляем главный заголовок как статический текст 
main_title = fig.text(0.5, 0.96, 'Принцип частотно-временной неопределённости\nв контексте сейсмической фильтрации', 
                     fontsize=16, fontweight='bold', ha='center', transform=fig.transFigure)

# Настройка осей (заголовки, пределы) - это делается один раз
# 1) Спектр фильтра
ax_filter_spec = axs[0, 0]
ax_filter_spec.set_title('1) Спектр фильтра')
ax_filter_spec.set_xlabel('Частота (Гц)')
ax_filter_spec.set_ylabel('Амплитуда')
ax_filter_spec.set_xlim(0, max_freq)
ax_filter_spec.set_ylim(-0.1, 1.1)

# 2) Сравнение спектров (перенесено в верхний ряд)
ax_spectra = axs[0, 1]
ax_spectra.set_title('2) Сравнение спектров')
ax_spectra.set_xlabel('Частота (Гц)')
ax_spectra.set_ylabel('Норм. амплитуда')
ax_spectra.set_xlim(0, max_freq)
ax_spectra.plot(freqs[freq_mask_125], trace_spectrum_abs[freq_mask_125]/trace_spectrum_abs.max(), label='Оригинал', alpha=0.7)
ax_spectra.legend(loc='upper right')

# 3) Импульсный отклик (перенесен в нижний ряд слева)
ax_impulse = axs[1, 0]
ax_impulse.set_title('3) Импульсный отклик фильтра')
ax_impulse.set_xlabel('Время (с)')
ax_impulse.set_ylabel('Амплитуда')
ax_impulse.set_xlim(-0.2, 0.2)

# 4) Сравнение трасс (перенесено в нижний ряд справа)
ax_traces = axs[1, 1]
ax_traces.set_title('4) Сравнение трасс')
ax_traces.set_xlabel('Амплитуда')
ax_traces.set_ylabel('Время (с)')
ax_traces.invert_yaxis()
ax_traces.plot(synthetic_trace, t, 'k', label='Оригинал', alpha=0.7)
ax_traces.legend(loc='upper right')

# Создание "пустых" артистов, которые будут обновляться
line_filter_spec, = ax_filter_spec.plot([], [], 'r-', lw=2)
line_impulse, = ax_impulse.plot([], [], 'b-')
line_filtered_trace, = ax_traces.plot([], [], 'r', label='Фильтрованная')
line_filtered_spectrum, = ax_spectra.plot([], [], 'r', label='Фильтрованный')

# Убираем динамический подзаголовок
fig.tight_layout(rect=[0, 0.03, 1, 0.94])

# Хранилище для fill_betweenx, т.к. его сложнее обновлять
fill_collection = []

# Функция инициализации (необязательна, если мы создали артистов выше)
def init():
    line_filter_spec.set_data([], [])
    line_impulse.set_data([], [])
    line_filtered_trace.set_data([], [])
    line_filtered_spectrum.set_data([], [])
    return line_filter_spec, line_impulse, line_filtered_trace, line_filtered_spectrum

# Функция обновления для каждого кадра
def update(frame):
    # Очищаем предыдущую заливку
    global fill_collection
    if fill_collection:
        for coll in fill_collection:
            coll.remove()
        fill_collection = []
        
    # Вычисляем данные для текущего кадра
    smoothing_level = int(frame * 1.0) # Увеличиваем сглаживание с каждым кадром
    
    # 1. Фильтр и его спектр (ограничено до 125 Гц)
    initial_filter_spec = trapezoidal_filter(freqs[freq_mask_125], *f_corners)
    smoothed_filter_spec = smooth_filter(initial_filter_spec, smoothing_level)
    line_filter_spec.set_data(freqs[freq_mask_125], smoothed_filter_spec)
    
    # 2. Импульсный отклик
    full_filter_spec = np.zeros_like(freqs, dtype=float)
    full_filter_spec[positive_freq_mask] = trapezoidal_filter(freqs[positive_freq_mask], *f_corners)
    full_filter_spec[~positive_freq_mask] = full_filter_spec[positive_freq_mask][::-1]
    # Применяем сглаживание к полному спектру
    full_filter_spec[positive_freq_mask] = smooth_filter(full_filter_spec[positive_freq_mask], smoothing_level)
    full_filter_spec[~positive_freq_mask] = full_filter_spec[positive_freq_mask][::-1]
    
    impulse_response = np.roll(np.real(ifft(full_filter_spec)), nt // 2)
    line_impulse.set_data(t - t.max()/2, impulse_response)
    ax_impulse.set_ylim(-0.12, 0.2) # Фиксированные пределы по y
    
    # 3. Фильтрация трассы
    filtered_trace_spec = fft(synthetic_trace) * full_filter_spec
    filtered_trace = np.real(ifft(filtered_trace_spec))
    line_filtered_trace.set_data(filtered_trace + 2.0, t) # Сдвигаем для наглядности
    
    # Добавляем новую заливку
    fill_pos = ax_traces.fill_betweenx(t, 2.0, filtered_trace + 2.0, where=(filtered_trace>0), color='red', alpha=0.5)
    fill_neg = ax_traces.fill_betweenx(t, 2.0, filtered_trace + 2.0, where=(filtered_trace<0), color='blue', alpha=0.5)
    fill_collection.extend([fill_pos, fill_neg])

    # 4. Спектр отфильтрованной трассы (ограничено до 125 Гц)
    filtered_spectrum_abs = np.abs(filtered_trace_spec)
    line_filtered_spectrum.set_data(freqs[freq_mask_125], filtered_spectrum_abs[freq_mask_125]/trace_spectrum_abs.max())
    
    # Возвращаем список всех измененных артистов
    return [line_filter_spec, line_impulse, line_filtered_trace, line_filtered_spectrum] + fill_collection


# Создание и запуск анимации 
#interval - задержка между кадрами в миллисекундах
#blit=True - оптимизация, перерисовывающая только измененные части
frames = np.arange(n_frames)
anim = FuncAnimation(fig, update, frames=frames, init_func=init, blit=True, interval=150)
#anim.save('freq_time_uncertainty_bpf.mp4', 
#      writer='ffmpeg', 
#      fps=5,           # кадров в секунду
#      bitrate=1800,     # битрейт для качества
#      extra_args=['-vcodec', 'libx264', '-pix_fmt', 'yuv420p'])

# Для отображения в Jupyter Notebook
plt.close(fig) # Предотвращаем отображение статической фигуры
HTML(anim.to_jshtml())